In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import time
from tqdm import tqdm
import itertools
import warnings

%matplotlib inline
warnings.filterwarnings('ignore')
pd.set_option('max_columns', None)
pd.set_option('max_rows', None)

from sklearn import preprocessing
from sklearn.decomposition import PCA
from sklearn.model_selection import StratifiedKFold, KFold
from sklearn.metrics import mean_absolute_error, mean_squared_error

import lightgbm as lgb

In [2]:
def reduce_mem_usage(df):
	"""
	iterate through all the columns of a dataframe and modify the data type to reduce memory usage.
	:param df:
	:return:
	"""
	start_mem = df.memory_usage().sum()
	print('Memory usage of dataframe is {:.2f} MB'.format(start_mem))

	for col in df.columns:
		col_type = df[col].dtype

		if col_type != object:
			c_min = df[col].min()
			c_max = df[col].max()
			if str(col_type)[:3] == 'int':
				if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
					df[col] = df[col].astype(np.int8)
				elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
					df[col] = df[col].astype(np.int16)
				elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
					df[col] = df[col].astype(np.int32)
				elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
					df[col] = df[col].astype(np.int64)
			else:
				if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
					df[col] = df[col].astype(np.float16)
				elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
					df[col] = df[col].astype(np.float32)
				else:
					df[col] = df[col].astype(np.float64)
		else:
			df[col] = df[col].astype('category')

	end_mem = df.memory_usage().sum()
	print('Memory usage after optimization is: {:.2f} MB'.format(end_mem))
	print('Decreased by {:.1f}%'.format(100 * (start_mem - end_mem) / start_mem))
	return df

In [3]:
def date_proc(x):
    # '20200426' '20200026'
    m = int(x[4:6])
    if m == 0:
        m = 1
    return x[:4] + '-' + str(m) + '-' + x[6:]

# 定义日期提取函数
def date_tran(df,fea_col):
    for f in tqdm(fea_col):
        df[f] = pd.to_datetime(df[f].astype('str').apply(date_proc))
        df[f + '_year'] = df[f].dt.year # 年份
        df[f + '_month'] = df[f].dt.month # 月份
        df[f + '_day'] = df[f].dt.day # 多少号
        df[f + '_dayofweek'] = df[f].dt.dayofweek # 周几
    return df

# 分桶操作
def cut_group(df, cols, num_bins=50):
    for col in cols:
#         all_range = int(df[col].max() - df[col].min())
#         bin = [i * all_range / num_bins for i in range(num_bins)]
        df[col + '_bin'] = pd.cut(df[col], num_bins, labels=False)
    return df

# count编码
def count_coding(df, fea_col):
    for f in fea_col:
        df[f + '_count'] = df[f].map(df[f].value_counts())
    return df

# 定义交叉特征统计
def cross_cat_num(df, num_col, cat_col):
    for f1 in tqdm(cat_col):
        g = df.groupby(f1, as_index=False)
        for f2 in tqdm(num_col):
            feat = g[f2].agg({
                '{}_{}_max'.format(f1, f2): 'max', # 最大值
                '{}_{}_min'.format(f1, f2): 'min', # 最小值
                '{}_{}_median'.format(f1, f2): 'median', # 中位数
            })
            df = df.merge(feat, on=f1, how='left')
    return df

In [4]:
Train_data = reduce_mem_usage(pd.read_csv('input/used_car_train_20200313.csv',
                                          sep=' '))
TestA_data = reduce_mem_usage(pd.read_csv('input/used_car_testB_20200421.csv',
                                          sep=' '))

print('Train data shape: {}'.format(Train_data.shape))
print('TestA_data shape: {}'.format(TestA_data.shape))

Memory usage of dataframe is 37200128.00 MB
Memory usage after optimization is: 10200232.00 MB
Decreased by 72.6%
Memory usage of dataframe is 12000128.00 MB
Memory usage after optimization is: 3200232.00 MB
Decreased by 73.3%
Train data shape: (150000, 31)
TestA_data shape: (50000, 30)


In [5]:
# 合并数据集
concat_data = pd.concat([Train_data, TestA_data],
                        ignore_index=True) # 重新生成索引

In [6]:
# 'notRepairedDamage'中的'-'用0替换
concat_data['notRepairedDamage'] = concat_data['notRepairedDamage'].replace('-', 0).astype('float16')

In [7]:
# 每列中的缺失值用每列的众数填充
# concat_data = concat_data.fillna(concat_data.mode().iloc[0, :])

In [8]:
concat_data.shape

(200000, 31)

In [9]:
# 处理异常值
concat_data['power'][concat_data['power'] > 600] = 600
concat_data['power'][concat_data['power'] < 1] = 1

concat_data['v_13'][concat_data['v_13'] > 6] = 6
concat_data['v_14'][concat_data['v_14'] > 4] = 4

In [10]:
# v系列特征之间相加
for j in ['v_' + str(i) for i in range(14)]:
    for k in ['v_' + str(m) for m in range(14)]:
        concat_data[j + '+' + k] = concat_data[j] + concat_data[k]

In [11]:
# 原始特征与v系列特征之间相乘
for i in ['model', 'brand', 'bodyType', 'fuelType', 'gearbox', 'power', 'kilometer', 'notRepairedDamage', 'regionCode']:
    for j in ['v_' + str(k) for k in range(14)]:
        concat_data[i + '*' + j] = concat_data[i] * concat_data[j]

In [12]:
concat_data.shape

(200000, 353)

In [13]:
# 提取日期信息
date_cols = ['regDate', 'creatDate']
concat_data = date_tran(concat_data, date_cols)

concat_data.shape

100%|████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00,  2.67it/s]


(200000, 361)

In [14]:
data = concat_data.copy()

print(data.columns)

Index(['SaleID', 'name', 'regDate', 'model', 'brand', 'bodyType', 'fuelType',
       'gearbox', 'power', 'kilometer',
       ...
       'regionCode*v_12', 'regionCode*v_13', 'regDate_year', 'regDate_month',
       'regDate_day', 'regDate_dayofweek', 'creatDate_year', 'creatDate_month',
       'creatDate_day', 'creatDate_dayofweek'],
      dtype='object', length=361)


In [15]:
# count编码
count_list = ['regDate', 'creatDate', 'model', 'brand', 'regionCode', 'bodyType', 'fuelType', 'name',
              'regDate_year', 'regDate_month', 'regDate_day', 'regDate_dayofweek',
              'creatDate_month', 'creatDate_day', 'creatDate_dayofweek', 'kilometer']

data = count_coding(data, count_list)

In [16]:
data['used_time1'] = (pd.to_datetime(data['creatDate'], format='%Y%m%d', errors='coerce') - 
                      pd.to_datetime(data['regDate'], format='%Y%m%d', errors='coerce')).dt.days
data['used_time2'] = (pd.datetime.now() - pd.to_datetime(data['regDate'], format='%Y%m%d', errors='coerce')).dt.days                        
data['used_time3'] = (pd.datetime.now() - pd.to_datetime(data['creatDate'], format='%Y%m%d', errors='coerce') ).dt.days

In [17]:
# 用数值特征对类别特征做统计刻画，随便挑了几个跟price相关性最高的匿名特征
cross_cat = ['model', 'brand', 'regDate_year']
cross_num = ['v_0', 'v_3', 'v_4', 'v_8', 'v_12', 'power', 'used_time1']
data = cross_cat_num(data, cross_num, cross_cat) # 一阶交叉

100%|████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:10<00:00,  3.51s/it]


In [18]:
# 选择特征列
numerical_cols = data.columns
print(numerical_cols)

Index(['SaleID', 'name', 'regDate', 'model', 'brand', 'bodyType', 'fuelType',
       'gearbox', 'power', 'kilometer',
       ...
       'regDate_year_v_8_median', 'regDate_year_v_12_max',
       'regDate_year_v_12_min', 'regDate_year_v_12_median',
       'regDate_year_power_max', 'regDate_year_power_min',
       'regDate_year_power_median', 'regDate_year_used_time1_max',
       'regDate_year_used_time1_min', 'regDate_year_used_time1_median'],
      dtype='object', length=443)


In [19]:
cat_fea = ['SaleID', 'offerType', 'seller']
feature_cols = [col for col in numerical_cols if col not in cat_fea]
feature_cols = [col for col in feature_cols if col not in ['price']]

# 将训练集和测试集分开
X_data = data.iloc[:len(Train_data), :][feature_cols]
Y_data = Train_data['price']
X_test = data.iloc[len(Train_data):, :][feature_cols]

In [20]:
import numpy as np
import pandas as pd
from sklearn.model_selection import StratifiedKFold, KFold
from itertools import product
class MeanEncoder:
    def __init__(self, categorical_features, n_splits=10, target_type='classification', prior_weight_func=None):
        """
        :param categorical_features: list of str, the name of the categorical columns to encode
 
        :param n_splits: the number of splits used in mean encoding
 
        :param target_type: str, 'regression' or 'classification'
 
        :param prior_weight_func:
        a function that takes in the number of observations, and outputs prior weight
        when a dict is passed, the default exponential decay function will be used:
        k: the number of observations needed for the posterior to be weighted equally as the prior
        f: larger f --> smaller slope
        """
 
        self.categorical_features = categorical_features
        self.n_splits = n_splits
        self.learned_stats = {}
 
        if target_type == 'classification':
            self.target_type = target_type
            self.target_values = []
        else:
            self.target_type = 'regression'
            self.target_values = None
 
        if isinstance(prior_weight_func, dict):
            self.prior_weight_func = eval('lambda x: 1 / (1 + np.exp((x - k) / f))', dict(prior_weight_func, np=np))
        elif callable(prior_weight_func):
            self.prior_weight_func = prior_weight_func
        else:
            self.prior_weight_func = lambda x: 1 / (1 + np.exp((x - 2) / 1))
 
    @staticmethod
    def mean_encode_subroutine(X_train, y_train, X_test, variable, target, prior_weight_func):
        X_train = X_train[[variable]].copy()
        X_test = X_test[[variable]].copy()
 
        if target is not None:
            nf_name = '{}_pred_{}'.format(variable, target)
            X_train['pred_temp'] = (y_train == target).astype(int)  # classification
        else:
            nf_name = '{}_pred'.format(variable)
            X_train['pred_temp'] = y_train  # regression
        prior = X_train['pred_temp'].mean()
 
        col_avg_y = X_train.groupby(by=variable, axis=0)['pred_temp'].agg(['mean', 'size'])
        col_avg_y['size'] = prior_weight_func(col_avg_y['size'])
        col_avg_y[nf_name] = col_avg_y['size'] * prior + (1 - col_avg_y['size']) * col_avg_y['mean']
        col_avg_y.drop(['size', 'mean'], axis=1, inplace=True)
 
        nf_train = X_train.join(col_avg_y, on=variable)[nf_name].values
        nf_test = X_test.join(col_avg_y, on=variable).fillna(prior, inplace=False)[nf_name].values
 
        return nf_train, nf_test, prior, col_avg_y
 
    def fit_transform(self, X, y):
        """
        :param X: pandas DataFrame, n_samples * n_features
        :param y: pandas Series or numpy array, n_samples
        :return X_new: the transformed pandas DataFrame containing mean-encoded categorical features
        """
        X_new = X.copy()
        if self.target_type == 'classification':
            skf = StratifiedKFold(self.n_splits)
        else:
            skf = KFold(self.n_splits)
 
        if self.target_type == 'classification':
            self.target_values = sorted(set(y))
            self.learned_stats = {'{}_pred_{}'.format(variable, target): [] for variable, target in
                                  product(self.categorical_features, self.target_values)}
            for variable, target in product(self.categorical_features, self.target_values):
                nf_name = '{}_pred_{}'.format(variable, target)
                X_new.loc[:, nf_name] = np.nan
                for large_ind, small_ind in skf.split(X, y):
                    nf_large, nf_small, prior, col_avg_y = MeanEncoder.mean_encode_subroutine(
                        X_new.iloc[large_ind], y.iloc[large_ind], X_new.iloc[small_ind], variable, target, self.prior_weight_func)
                    X_new.iloc[small_ind, -1] = nf_small
                    self.learned_stats[nf_name].append((prior, col_avg_y))
        else:
            self.learned_stats = {'{}_pred'.format(variable): [] for variable in self.categorical_features}
            for variable in self.categorical_features:
                nf_name = '{}_pred'.format(variable)
                X_new.loc[:, nf_name] = np.nan
                for large_ind, small_ind in skf.split(X, y):
                    nf_large, nf_small, prior, col_avg_y = MeanEncoder.mean_encode_subroutine(
                        X_new.iloc[large_ind], y.iloc[large_ind], X_new.iloc[small_ind], variable, None, self.prior_weight_func)
                    X_new.iloc[small_ind, -1] = nf_small
                    self.learned_stats[nf_name].append((prior, col_avg_y))
        return X_new
 
    def transform(self, X):
        """
        :param X: pandas DataFrame, n_samples * n_features
        :return X_new: the transformed pandas DataFrame containing mean-encoded categorical features
        """
        X_new = X.copy()
 
        if self.target_type == 'classification':
            for variable, target in product(self.categorical_features, self.target_values):
                nf_name = '{}_pred_{}'.format(variable, target)
                X_new[nf_name] = 0
                for prior, col_avg_y in self.learned_stats[nf_name]:
                    X_new[nf_name] += X_new[[variable]].join(col_avg_y, on=variable).fillna(prior, inplace=False)[
                        nf_name]
                X_new[nf_name] /= self.n_splits
        else:
            for variable in self.categorical_features:
                nf_name = '{}_pred'.format(variable)
                X_new[nf_name] = 0
                for prior, col_avg_y in self.learned_stats[nf_name]:
                    X_new[nf_name] += X_new[[variable]].join(col_avg_y, on=variable).fillna(prior, inplace=False)[
                        nf_name]
                X_new[nf_name] /= self.n_splits
 
        return X_new

In [21]:
class_list = ['model', 'brand', 'name', 'regionCode'] + date_cols
MeanEncodeFeature = class_list
ME = MeanEncoder(categorical_features=MeanEncodeFeature, n_splits=5, target_type='regression', prior_weight_func=None)
X_data = ME.fit_transform(X_data, Y_data)
X_test = ME.transform(X_test)

In [22]:
X_data['price'] = Train_data['price']

In [23]:
# target encoding目标编码，回归场景相对来说做目标编码的选择更多，不仅可以做均值编码，还可以做标准差编码、中位数编码等
enc_cols = []
stats_default_dict = {
    'max': X_data['price'].max(),
    'min': X_data['price'].min(),
    'median': X_data['price'].median(),
    'mean': X_data['price'].mean(),
    'sum': X_data['price'].sum(),
    'std': X_data['price'].std(),
    'skew': X_data['price'].skew(), # 偏度
    'kurt': X_data['price'].kurt(), # 峰度
    'mad': X_data['price'].mad() # mean absolute deviation 平均绝对偏差
}

# 暂且选择这三种编码
enc_stats = ['max', 'min', 'mean']
skf = KFold(n_splits=10, shuffle=True, random_state=42)
for f in tqdm(['regionCode', 'brand', 'regDate_year' ,'creatDate_year', 'kilometer', 'model']):
    enc_dict = {}
    for stat in enc_stats:
        enc_dict['{}_target_{}'.format(f, stat)] = stat
        X_data['{}_target_{}'.format(f, stat)] = 0
        X_test['{}_target_{}'.format(f, stat)] = 0
        enc_cols.append('{}_target_{}'.format(f, stat))
    for i, (trn_idx, val_idx) in enumerate(skf.split(X_data, Y_data)):
        trn_x, val_x = X_data.iloc[trn_idx].reset_index(drop=True), X_data.iloc[val_idx].reset_index(drop=True)
        enc_df = trn_x.groupby(f, as_index=False)['price'].agg(enc_dict)
        val_x = val_x[[f]].merge(enc_df, on=f, how='left')
        test_x = X_test[[f]].merge(enc_df, on=f, how='left')
        for stat in enc_stats:
            val_x['{}_target_{}'.format(f, stat)] = val_x['{}_target_{}'.format(f, stat)].fillna(stats_default_dict[stat])
            test_x['{}_target_{}'.format(f, stat)] = test_x['{}_target_{}'.format(f, stat)].fillna(stats_default_dict[stat])
            X_data.loc[val_idx, '{}_target_{}'.format(f, stat)] = val_x['{}_target_{}'.format(f, stat)].values 
            X_test['{}_target_{}'.format(f, stat)] += test_x['{}_target_{}'.format(f, stat)].values / skf.n_splits

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:23<00:00,  3.89s/it]


In [24]:
drop_list = ['regDate', 'creatDate', 'brand_power_min', 'regDate_year_power_min']
x_train = X_data.drop(drop_list + ['price'], axis=1)
x_test = X_test.drop(drop_list, axis=1)
x_train.shape

(150000, 459)

In [25]:
x_train = x_train.astype('float32')
x_test = x_test.astype('float32')

In [ ]:
from sklearn.feature_selection import RFECV

lgb_model = lgb.LGBMRegressor(objective='regression_l1', random_state=666)

rfecv = RFECV(estimator=lgb_model,
              cv=5,
              step=2, # 每步删除的特征个数
              scoring='neg_mean_absolute_error', # 打分函数
              n_jobs=-1)
rfecv.fit(x_train, Train_data['price'])

print(rfecv.n_features_) # 选中的特征个数
print(rfecv.ranking_) # 特征排名

feats = list(np.array(train_x.columns)[rfecv.support_]) # 选中的特征
feats

In [30]:
params = {'objective': 'regression_l1',
          'boosting': 'gbdt',
          'metric': 'mae',
          'learning_rate': 0.2,
          'num_leaves': 31,
          'seed': 2020}

lgb_train = lgb.Dataset(X_pca, label=y)

cv_results = lgb.cv(params,
                    lgb_train,
                    num_boost_round=100000,
                    early_stopping_rounds=200,
                    eval_train_metric=True)
cv_df = pd.DataFrame(cv_results)
cv_df

train l1-mean  train l1-stdv  valid l1-mean  valid l1-stdv
0        4658.249107       4.471435    4660.137365       9.311123
1        4348.174806       6.062077    4351.231498       6.621706
2        4067.433697       3.121821    4071.827029      12.459090
3        3804.381631       6.785858    3809.906410       9.392589
4        3574.338750       4.187001    3581.566790       8.416809
5        3358.857348       8.590553    3366.748324       7.788220
6        3169.735119       3.986925    3178.603836       9.835560
7        2993.169660       7.704309    3003.795419       5.606675
8        2832.125943      10.341743    2843.693361       4.952894
9        2688.476407      11.528155    2700.627803       6.548411
10       2552.211464      11.049094    2565.433957       6.524000
11       2432.270780      11.410949    2446.822873       5.708154
12       2322.626438       9.367440    2338.394447       6.366416
13       2224.962392       8.684858    2242.209662       6.880362
14       2133.848937       7.979572    2152.476873       5.573728
15       2048.629984       6.836140    2068.463679       7.794208
16       1969.513475       6.444425    1991.109888       6.940320
17       1899.097525       4.551041    1922.083575       7.540760
18       1837.388159       4.081396    1861.528795       9.111470
19       1777.492520       5.084141    1803.052986       8.374574
20       1724.286956       3.656464    1750.681565      10.188203
21       1675.726196       4.867813    1703.797341      10.769991
22       1630.828876       5.644000    1660.191714      10.056732
23       1589.799879       5.908925    1620.380394      10.456177
24       1552.051027       5.115600    1583.837635      10.406825
25       1518.246806       6.588712    1551.033485       9.312075
26       1486.767998       6.948725    1520.506931      10.680737
27       1457.508159       7.042540    1492.129947       9.564169
28       1430.343068       6.896055    1465.717144       9.482795
29       1406.101678       5.841412    1442.516636       9.395619
30       1384.008200       5.531703    1421.467236       9.519921
31       1364.042186       4.763944    1402.473176       9.750053
32       1345.746894       4.486735    1385.244595       9.520385
33       1329.579133       4.720651    1370.062871       9.629629
34       1314.709265       4.183129    1356.114245       9.495490
35       1300.333924       3.917328    1342.702247       9.042761
36       1287.018588       4.556090    1330.222518       8.732532
37       1274.699988       4.275046    1318.777561       8.519634
38       1263.902987       4.302970    1308.778235       8.708201
39       1253.550391       4.075452    1299.438634       8.301365
40       1243.979369       4.247714    1290.432204       7.951756
41       1235.363777       4.028312    1282.398692       7.761579
42       1226.367298       3.563073    1274.369503       8.470926
43       1218.262664       4.222769    1267.063705       7.539581
44       1210.557613       3.668881    1260.011646       8.113443
45       1203.427281       4.207858    1253.692472       7.502281
46       1197.044642       3.792218    1247.938480       7.817009
47       1190.594475       4.017218    1242.300172       7.323169
48       1184.437015       4.225118    1236.845394       6.985653
49       1178.983118       4.212979    1232.051501       6.995528
50       1173.648499       4.100431    1227.263674       7.122303
51       1168.151030       4.295298    1222.333070       7.035612
52       1163.428217       4.215659    1218.643665       6.565647
53       1158.434037       3.781514    1214.656899       6.474851
54       1153.835760       3.684879    1210.883725       6.753183
55       1149.091237       3.502355    1206.789817       7.093862
56       1144.682372       3.471794    1203.130709       7.234035
57       1140.210222       3.267930    1199.261950       7.416767
58       1136.185147       2.904627    1195.869492       7.671731
59       1131.848216       2.700658    1192.132

In [31]:
lgb_model = lgb.train(params,
                      lgb_train,
                      valid_sets=lgb_train,
                      num_boost_round=len(cv_df),
                      early_stopping_rounds=200,
                      verbose_eval=300)

Training until validation scores don't improve for 200 rounds
[300]	training's l1: 802.647
[600]	training's l1: 668.287
[900]	training's l1: 585.122
[1200]	training's l1: 522.974
[1500]	training's l1: 472.264
[1800]	training's l1: 430.551
[2100]	training's l1: 395.059
[2400]	training's l1: 364.219
[2700]	training's l1: 337.476
[3000]	training's l1: 312.122
[3300]	training's l1: 289.528
[3600]	training's l1: 269.335
[3900]	training's l1: 251.304
[4200]	training's l1: 234.903
[4500]	training's l1: 219.332
[4800]	training's l1: 205.368
[5100]	training's l1: 192.404
[5400]	training's l1: 180.448
[5700]	training's l1: 169.323
[6000]	training's l1: 159.054
[6300]	training's l1: 149.562
[6600]	training's l1: 140.838
[6900]	training's l1: 132.595
[7200]	training's l1: 124.822
[7500]	training's l1: 117.429
[7800]	training's l1: 110.729
[8100]	training's l1: 104.28
[8400]	training's l1: 98.3104
[8700]	training's l1: 92.7762
[9000]	training's l1: 87.5051
[9300]	training's l1: 82.6123
[9600]	train

In [32]:
TestA_data['price'] = lgb_model.predict(test)

TestA_data[['SaleID', 'price']].to_csv('submit/lgb_sub_{}_{}.csv'.format('mae', int(TestA_data['price'].mean())), index=False)